# Federated ImgOnly

In [1]:
# Install dependencies if not already installed
import os
import pandas as pd
import PIL
from PIL import Image

import tqdm
import numpy as np
import torch
import torchvision
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader, random_split
from torchvision import utils, transforms
import torch.nn.functional as F

import glob
import nibabel as nib
import time

from torch.utils.tensorboard import SummaryWriter

/home/user1/anaconda3/envs/adni_fl/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
!ls /home/user1/fast_storage

a1	AD			     AD.zip
a1.zip	ADNI2_Img_only.ipynb	     check_tensorboards.ipynb
a2	ADNI2_Img_only-JRIEKE.ipynb  move_T1.ipynb
a2.zip	ADNI2_multi-input.ipynb      Multi_input_federated
a3	ADNI2_txt_only.ipynb	     runs
a3.zip	ADNI_csv


## Connect to the Federation

In [3]:
# Create a federation
from openfl.interface.interactive_api.federation import Federation

# please use the same identificator that was used in signed certificate
client_id = 'api'
director_node_fqdn = 'ai2'
director_port=50051

# 2) Run with TLS disabled (trusted environment)
# Federation can also determine local fqdn automatically
federation = Federation(
    client_id=client_id,
    director_node_fqdn=director_node_fqdn,
    director_port=director_port, 
    tls=False
)


In [4]:
shard_registry = federation.get_shard_registry()
shard_registry

{'adni1': {'shard_info': node_info {
    name: "adni1"
  }
  shard_description: "MultiINPUT dataset, shard number 1 out of 1"
  sample_shape: "90"
  sample_shape: "109"
  sample_shape: "90"
  target_shape: "1"
  target_shape: "1",
  'is_online': True,
  'is_experiment_running': False,
  'last_updated': '2023-01-31 20:56:30',
  'current_time': '2023-01-31 20:57:16',
  'valid_duration': seconds: 120,
  'experiment_name': 'ExperimentName Mock'},
 'adni2': {'shard_info': node_info {
    name: "adni2"
  }
  shard_description: "MultiINPUT dataset, shard number 1 out of 1"
  sample_shape: "90"
  sample_shape: "109"
  sample_shape: "90"
  target_shape: "1"
  target_shape: "1",
  'is_online': True,
  'is_experiment_running': False,
  'last_updated': '2023-01-31 20:56:33',
  'current_time': '2023-01-31 20:57:16',
  'valid_duration': seconds: 120,
  'experiment_name': 'ExperimentName Mock'},
 'adni3': {'shard_info': node_info {
    name: "adni3"
  }
  shard_description: "MultiINPUT dataset, shard

In [5]:
# First, request a dummy_shard_desc that holds information about the federated dataset 
dummy_shard_desc = federation.get_dummy_shard_descriptor(size=10)
dummy_shard_dataset = dummy_shard_desc.get_dataset('train')
sample, target = dummy_shard_dataset[0]
f"Sample shape: {sample.shape}, target shape: {target.shape}"

'Sample shape: (90, 109, 90), target shape: (1, 1)'

## Describing FL experimen

In [6]:
from openfl.interface.interactive_api.experiment import TaskInterface, DataInterface, ModelInterface, FLExperiment

## Load MedMNIST INFO

#### Parameters

In [7]:
batch_size = 8
experiment_name= "FL_img_only"
epochs = 200

myseed = 11
torch.manual_seed(myseed)
np.random.seed(myseed)
generator = torch.Generator()
generator.manual_seed(myseed)


num_classes=1

experiment_name = experiment_name + "_" + str(myseed)
print(f"{experiment_name}")


FL_img_only_11


### Register dataset

In [8]:
#from wspace_utils.utils import Transform3D, model_to_syncbn
#shape_transform = False

#train_transform = Transform3D(mul='random') if shape_transform else Transform3D()
#eval_transform = Transform3D(mul='0.5') if shape_transform else Transform3D()

In [9]:
class TransformedDataset(Dataset):
    """Data extraction"""

    def __init__(self, input_dataframe, transform=None):
        """Initialize Dataset."""
        self.input_df = input_dataframe
        self.transform = transform

    def __len__(self):
        """Length of dataset."""
        return len(self.input_df)

    def __getitem__(self, idx):
        if torch.is_tensor(idx):
            idx = index.tolist()

        line = self.input_df[idx]#[idx, 0:]
        
        # Get Label
        y = line['labels']
                   
        # Get image
        img_path= os.path.join('/home/user1/fast_storage',line['IMG_PATH'])
        image = nib.load(img_path)
        image = image.get_fdata() 
        
        if self.transform is not None:
            img = self.transform(img)

        image = transforms.functional.to_tensor(image)
        image = image.unsqueeze(dim=0)
        
        return image, y

In [10]:
class MultiINPUTFedDataset(DataInterface):
    def __init__(self, **kwargs):
        self.kwargs = kwargs
        
    @property
    def shard_descriptor(self):
        return self._shard_descriptor
        
    @shard_descriptor.setter
    def shard_descriptor(self, shard_descriptor):
        """
        Describe per-collaborator procedures or sharding.

        This method will be called during a collaborator initialization.
        Local shard_descriptor  will be set by Envoy.
        """
        self._shard_descriptor = shard_descriptor

        self.train_set = TransformedDataset(
            self._shard_descriptor.get_dataset('train'),
            transform=None
        )       
        
        self.valid_set = TransformedDataset(
            self._shard_descriptor.get_dataset('val'),
            transform=None
        )
        
    def get_train_loader(self, **kwargs):
        """
        Output of this method will be provided to tasks with optimizer in contract
        """
        return DataLoader(
            self.train_set, num_workers=1, batch_size=self.kwargs['train_bs'], shuffle=True)

    def get_valid_loader(self, **kwargs):
        """
        Output of this method will be provided to tasks without optimizer in contract
        """
        return DataLoader(self.valid_set, num_workers=1, batch_size=self.kwargs['valid_bs'])

    def get_train_data_size(self):
        """
        Information for aggregation
        """
        return len(self.train_set)

    def get_valid_data_size(self):
        """
        Information for aggregation
        """
        return len(self.valid_set)
    

### Create Mnist federated dataset

In [11]:
fed_dataset = MultiINPUTFedDataset(train_bs=8, valid_bs=8, test_bs=8)

In [12]:
#fed_dataset.shard_descriptor = dummy_shard_desc
#for i, (sample, tab, target) in enumerate(fed_dataset.get_train_loader()):
#    sample = (np.array(sample))
#    print(sample.shape, tab.shape, target.shape)
    
#print(f"dtype = {sample.dtype}, type = {type(sample)}")

## Describe the model and optimizer

## IMG-Only Net

In [13]:
def get_inplanes():
    return [64, 128, 256, 512]


def conv3x3x3(in_planes, out_planes, stride=1):
    return nn.Conv3d(in_planes,
                     out_planes,
                     kernel_size=3,
                     stride=stride,
                     padding=1,
                     bias=False)


def conv1x1x1(in_planes, out_planes, stride=1):
    return nn.Conv3d(in_planes,
                     out_planes,
                     kernel_size=1,
                     stride=stride,
                     bias=False)


class BasicBlock(nn.Module):
    expansion = 1

    def __init__(self, in_planes, planes, stride=1, downsample=None):
        super().__init__()

        self.conv1 = conv3x3x3(in_planes, planes, stride)
        self.bn1 = nn.BatchNorm3d(planes)
        self.relu = nn.ReLU(inplace=True)
        self.conv2 = conv3x3x3(planes, planes)
        self.bn2 = nn.BatchNorm3d(planes)
        self.downsample = downsample
        self.stride = stride

    def forward(self, x):
        residual = x

        out = self.conv1(x)
        out = self.bn1(out)
        out = self.relu(out)

        out = self.conv2(out)
        out = self.bn2(out)

        if self.downsample is not None:
            residual = self.downsample(x)

        out += residual
        out = self.relu(out)

        return out


class Bottleneck(nn.Module):
    expansion = 4

    def __init__(self, in_planes, planes, stride=1, downsample=None):
        super().__init__()

        self.conv1 = conv1x1x1(in_planes, planes)
        self.bn1 = nn.BatchNorm3d(planes)
        self.conv2 = conv3x3x3(planes, planes, stride)
        self.bn2 = nn.BatchNorm3d(planes)
        self.conv3 = conv1x1x1(planes, planes * self.expansion)
        self.bn3 = nn.BatchNorm3d(planes * self.expansion)
        self.relu = nn.ReLU(inplace=True)
        self.downsample = downsample
        self.stride = stride

    def forward(self, x):
        residual = x

        out = self.conv1(x)
        out = self.bn1(out)
        out = self.relu(out)

        out = self.conv2(out)
        out = self.bn2(out)
        out = self.relu(out)

        out = self.conv3(out)
        out = self.bn3(out)

        if self.downsample is not None:
            residual = self.downsample(x)

        out += residual
        out = self.relu(out)

        return out


class ResNet(nn.Module):

    def __init__(self,
                 block,
                 layers,
                 block_inplanes,
                 n_input_channels=3,
                 conv1_t_size=7,
                 conv1_t_stride=1,
                 no_max_pool=False,
                 shortcut_type='B',
                 widen_factor=1.0,
                 n_classes=400):
        super().__init__()

        block_inplanes = [int(x * widen_factor) for x in block_inplanes]

        self.in_planes = block_inplanes[0]
        self.no_max_pool = no_max_pool

        self.conv1 = nn.Conv3d(n_input_channels,
                               self.in_planes,
                               kernel_size=(conv1_t_size, 7, 7),
                               stride=(conv1_t_stride, 2, 2),
                               padding=(conv1_t_size // 2, 3, 3),
                               bias=False)
        self.bn1 = nn.BatchNorm3d(self.in_planes)
        self.relu = nn.ReLU(inplace=True)
        self.maxpool = nn.MaxPool3d(kernel_size=3, stride=2, padding=1)
        self.layer1 = self._make_layer(block, block_inplanes[0], layers[0],
                                       shortcut_type)
        self.layer2 = self._make_layer(block,
                                       block_inplanes[1],
                                       layers[1],
                                       shortcut_type,
                                       stride=2)
        self.layer3 = self._make_layer(block,
                                       block_inplanes[2],
                                       layers[2],
                                       shortcut_type,
                                       stride=2)
        self.layer4 = self._make_layer(block,
                                       block_inplanes[3],
                                       layers[3],
                                       shortcut_type,
                                       stride=2)

        self.avgpool = nn.AdaptiveAvgPool3d((1, 1, 1))
        self.fc = nn.Linear(block_inplanes[3] * block.expansion, n_classes)

        for m in self.modules():
            if isinstance(m, nn.Conv3d):
                nn.init.kaiming_normal_(m.weight,
                                        mode='fan_out',
                                        nonlinearity='relu')
            elif isinstance(m, nn.BatchNorm3d):
                nn.init.constant_(m.weight, 1)
                nn.init.constant_(m.bias, 0)

    def _downsample_basic_block(self, x, planes, stride):
        out = F.avg_pool3d(x, kernel_size=1, stride=stride)
        zero_pads = torch.zeros(out.size(0), planes - out.size(1), out.size(2),
                                out.size(3), out.size(4))
        if isinstance(out.data, torch.FloatTensor):
            zero_pads = zero_pads

        out = torch.cat([out.data, zero_pads], dim=1)

        return out

    def _make_layer(self, block, planes, blocks, shortcut_type, stride=1):
        downsample = None
        if stride != 1 or self.in_planes != planes * block.expansion:
            if shortcut_type == 'A':
                downsample = partial(self._downsample_basic_block,
                                     planes=planes * block.expansion,
                                     stride=stride)
            else:
                downsample = nn.Sequential(
                    conv1x1x1(self.in_planes, planes * block.expansion, stride),
                    nn.BatchNorm3d(planes * block.expansion))

        layers = []
        layers.append(
            block(in_planes=self.in_planes,
                  planes=planes,
                  stride=stride,
                  downsample=downsample))
        self.in_planes = planes * block.expansion
        for i in range(1, blocks):
            layers.append(block(self.in_planes, planes))

        return nn.Sequential(*layers)

    def forward(self, x):
        x = self.conv1(x)
        x = self.bn1(x)
        x = self.relu(x)
        if not self.no_max_pool:
            x = self.maxpool(x)

        x = self.layer1(x)
        x = self.layer2(x)
        x = self.layer3(x)
        x = self.layer4(x)

        x = self.avgpool(x)

        x = x.view(x.size(0), -1)
        x = self.fc(x)

        return x


def ResNet18(in_channels, num_classes):
    return ResNet(BasicBlock, [2, 2, 2, 2], in_channels=in_channels, num_classes=num_classes)


def generate_model(model_depth, **kwargs):
    assert model_depth in [10, 18, 34, 50, 101, 152, 200]

    if model_depth == 10:
        model = ResNet(BasicBlock, [1, 1, 1, 1], get_inplanes(), **kwargs)
    elif model_depth == 18:
        model = ResNet(BasicBlock, [2, 2, 2, 2], get_inplanes(), **kwargs)
    elif model_depth == 34:
        model = ResNet(BasicBlock, [3, 4, 6, 3], get_inplanes(), **kwargs)
    elif model_depth == 50:
        model = ResNet(Bottleneck, [3, 4, 6, 3], get_inplanes(), **kwargs)
    elif model_depth == 101:
        model = ResNet(Bottleneck, [3, 4, 23, 3], get_inplanes(), **kwargs)
    elif model_depth == 152:
        model = ResNet(Bottleneck, [3, 8, 36, 3], get_inplanes(), **kwargs)
    elif model_depth == 200:
        model = ResNet(Bottleneck, [3, 24, 36, 3], get_inplanes(), **kwargs)

    return model


model = generate_model(18, n_input_channels=1,
                 widen_factor=1.0,
                 n_classes=1)
model = model.double()
print(model)

print('Total Parameters:',
      sum([torch.numel(p) for p in model.parameters()]))
print('Trainable Parameters:',
      sum([torch.numel(p) for p in model.parameters() if p.requires_grad]))

ResNet(
  (conv1): Conv3d(1, 64, kernel_size=(7, 7, 7), stride=(1, 2, 2), padding=(3, 3, 3), bias=False)
  (bn1): BatchNorm3d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool3d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv3d(64, 64, kernel_size=(3, 3, 3), stride=(1, 1, 1), padding=(1, 1, 1), bias=False)
      (bn1): BatchNorm3d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu): ReLU(inplace=True)
      (conv2): Conv3d(64, 64, kernel_size=(3, 3, 3), stride=(1, 1, 1), padding=(1, 1, 1), bias=False)
      (bn2): BatchNorm3d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (1): BasicBlock(
      (conv1): Conv3d(64, 64, kernel_size=(3, 3, 3), stride=(1, 1, 1), padding=(1, 1, 1), bias=False)
      (bn1): BatchNorm3d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)

In [14]:
## Model Params
optimizer = optim.Adam(model.parameters(), lr = 0.0001)
## Define a loss 
criterion = nn.BCEWithLogitsLoss()

### Register model

In [15]:
from copy import deepcopy

framework_adapter = 'openfl.plugins.frameworks_adapters.pytorch_adapter.FrameworkAdapterPlugin'
MI = ModelInterface(model=model, optimizer=optimizer, framework_plugin=framework_adapter)

# Save the initial model state
initial_model = deepcopy(model)

## Define and register FL tasks

In [16]:
TI = TaskInterface()

train_custom_params={'criterion':criterion}

# Task interface currently supports only standalone functions.
@TI.add_kwargs(**train_custom_params)
@TI.register_fl_task(model='model', data_loader='train_loader',
                     device='device', optimizer='optimizer')
def train(model, train_loader, device, optimizer, criterion):
    
    train_loader = tqdm.tqdm(train_loader, desc="train")
    
    total_loss, total_acc, total_samples = [],0,0
    #scheduler = torch.optim.lr_scheduler.OneCycleLR(optimizer, max_lr = 0.01, epochs=epochs, steps_per_epoch=len(train_loader))    
    model.train()
    model.to(device)
    
    for img, labels in train_loader: 
        img, labels = torch.tensor(img).to(device), torch.tensor(labels).to(device, dtype=torch.int64)
        optimizer.zero_grad()
        
        # Compute output
        pred = model(img)
        labels = labels.unsqueeze(1)
        labels = labels.float()
        loss = criterion(pred.float(), labels)
        loss.backward()
        optimizer.step()
        
        # update loss
        total_loss.append(loss.item())
        pred_labels = (pred >= 0).float() # Binarize predictions to 0 and 1
        batch_accuracy = (pred_labels == labels).sum().item()/img.size(0)
        # Update accuracy
        total_acc += batch_accuracy

    return {'train_loss': np.mean(total_loss), 
            'train_acc': total_acc/len(train_loader)}


val_custom_params={'criterion':criterion}

@TI.add_kwargs(**val_custom_params)
@TI.register_fl_task(model='model', data_loader='val_loader', device='device')
def validate(model, val_loader, device, criterion):

    val_loader = tqdm.tqdm(val_loader, desc="validate")
    total_loss, total_acc, total_samples = [],0,0
    
    model.eval()
    model.to(device)
    with torch.no_grad():
        for img, labels in val_loader:
            img, labels = torch.tensor(img).to(device), torch.tensor(labels).to(device, dtype=torch.int64)

            # Compute output
            pred = model(img)
            labels = labels.unsqueeze(1)
            labels = labels.float()
            loss = criterion(pred.float(), labels)  
            
            # update loss
            total_loss.append(loss.item())
            pred_labels = (pred >= 0).float()
            
             # Binarize predictions to 0 and 1
            batch_accuracy = (pred_labels == labels).sum().item()/img.size(0)
            # Update accuracy
            total_acc += batch_accuracy

        return {'val_loss': np.mean(total_loss),
                'val_acc': total_acc/len(val_loader)}

## Time to start a federated learning experiment

In [17]:
# create an experimnet in federation
fl_experiment = FLExperiment(federation=federation, experiment_name=experiment_name)

In [18]:
# The following command zips the workspace and python requirements to be transfered to collaborator nodes
fl_experiment.start(model_provider=MI, 
                    task_keeper=TI,
                    data_loader=fed_dataset,
                    rounds_to_train=epochs,
                    opt_treatment='RESET',
                    device_assignment_policy='CUDA_PREFERRED',
                    pip_install_options="")

/home/user1/.local/lib/python3.8/site-packages/_distutils_hack/__init__.py:33: UserWarning: Setuptools is replacing distutils.
  warnings.warn("Setuptools is replacing distutils.")


In [19]:
# If user want to stop IPython session, then reconnect and check how experiment is going
fl_experiment.restore_experiment_state(MI)
fl_experiment.stream_metrics(tensorboard_logs=True)

### 

In [ ]:
FLexperiment.get_best_model()

In [ ]:
!python3 -c "import pathlib;import importlib.util;s=importlib.util.find_spec('triton'); affected=any(x.name == 'triton' for x in (pathlib.Path(s.submodule_search_locations[0] if s is not None else '/' ) / 'runtime').glob('*'));print('You are {}affected'.format('' if affected else 'not '))"